In [2]:
import pandas as pd
import pickle
import os
import numpy as np
import random
from colog.colog import colog
from datetime import datetime, timedelta
c = colog()

In [3]:
def load_data_one_stock(path):
  load_data = pd.DataFrame()
  try:
    file = open(path, 'rb')
    load_data= pickle.load(file)
    file.close()
  except Exception as e:
    a = 1
    # print(e)
  return load_data

In [4]:
# SETTINGS
# stock_name_list  = ['AAPL','V', 'AMD', 'MSFT', 'MA', 'NVDA']
# stock_name_list  = ['GOOGL','CVS', 'AMZN', 'CRM', 'DIS', 'MCD']

# stock_name_list  = ['AAPL','V', 'AMD', 'MSFT', 'MA', 'NVDA'] + ['GOOGL','CVS', 'AMZN', 'CRM', 'DIS', 'MCD']
stock_name_list = []
stock_name_list += ['GOOG','JPM','XOM','UNH','JNJ','V','AVGO','PG','LLY','MA','HD','CVX','MRK', 
                       'PEP','COST','ABBV','ADBE','KO','CRM','WMT','MCD','CSCO','BAC','PFE','TMO','ACN','NFLX','ABT','AMD','LIN','ORCL','CMCSA',
                       'TXN','DIS','WFC','DHR','PM','NEE','VZ','INTC','RTX','HON','LOW','UPS','INTU','SPGI','NKE','COP','QCOM','BMY','CAT','UNP','BA','ISRG',
                        'GE','IBM','AMGN','AMAT','MDT','SBUX','PLD','NOW','MS','DE','BLK','GS','T','LMT','AXP','SYK','ADI','TJX','ELV','MDLZ','GILD','ADP','MMC',
                        'C','AMT','CVS','VRTX','SCHW','LRCX','MO','TMUS','SLB', 'ETN', 'ZTS', 'CI', 'PYPL']

stock_name_list += ['FI','CB','SO','REGN','BSX','EQIX','BDX','PANW','DUK','EOG','MU','AON','ITW','CSX','SNPS','PGR','APD','KLAC','CME','NOC','CDNS','ICE',
                       'CL','SHW','WM','HCA','TGT','FCX','FDX','F','MMM','CMG','EW','GM','MCK','NXPI','MCO','NSC','HUM','EMR','DXCM','PNC','PH','MPC','APH',
                       'ROP','FTNT','MCHP','PXD','USB','CCI','MAR','MSI','GD','PSA','JCI','PSX','SRE','ADSK','AZO','TDG','ECL','AJG','KMB','TEL','TT','AEP','EL','PCAR',
                       'OXY','TFC','CARR','D','IDXX','GIS','ON','COF','ADM','MNST','NUE','CTAS','AIG','EXC','VLO','MRNA','ANET','WMB','O','STZ','IQV','HLT','CHTR','WELL',
                       'BIIB','SPG','MSCI','DHI','ROK']

# dataset_name = 'periodmaxinterval1m'
dataset_name = 'period90interval1m'
folder_saved_models = f'historical_data\\{dataset_name}'
file_suffix = 'period90_interval1m.pkl'
parent_path = os.getcwd()
buy_money = 2000
commission_value = 0.0005
trainig_part = 0.5
test_part = 0.5

Exlude companies with bad ration and retraining!!!

Currten best settings:
{'is_near_global_max_prt': 0, 'distance_from_last_top': 2, 'last_top_ratio': 1, 'RIV': 0.2, 'buy_ratio_border': 10}
-3458.0764813327787 495


In [5]:
## Load data S&P500 index

# file_name = 'df_stock_^GSPC_periodmax_interval1m.pkl'
# path = os.path.join(parent_path, folder_saved_models, file_name)
# df_SP500 = load_data_one_stock(path)


In [6]:
def is_near_global_max(i, k=400, prt=70):
  result = False
  try:
    if i > k:
      gmax = max(df['close'].iloc[i - k: i])
      reference_point = df['close'].iloc[i - k]
      gmin = min(df['close'].iloc[i - k: i])
    else:
      reference_point = df['close'].iloc[0]
      gmax = max(df['close'].iloc[0: i])
      gmin = min(df['close'].iloc[0: i])
    result = 100 * (df['close'].iloc[i] - gmin) / (gmax - gmin) > prt
  except Exception as e:
    alarm.print(e)

  return result

def global_max_prop(i, k=40):

  if i > k:
   gmax = max(df['close'].iloc[i - k: i])
   gmin = min(df['close'].iloc[i - k: i])
  else:
   gmax = max(df['close'].iloc[0: i])
   gmin = min(df['close'].iloc[0: i])

  return gmax / gmin

def number_red_candles(df, i, k=11):

  if i < k:
    number_red_candles = (df['ha_colour'][0 : i] == 'red').sum()
  else:
    number_red_candles = (df['ha_colour'][i - k : i] == 'red').sum()
  return number_red_candles

def number_green_candles(df, i, k=11):

  if i < k:
    number_green_candles = (df['ha_colour'][0 : i] == 'green').sum()
  else:
    number_green_candles = (df['ha_colour'][i - k : i] == 'green').sum()
  return number_green_candles

In [7]:
def one_stock_simulation(df, ticker, mode, _gain_coef = 1.005, _lose_coef = 0.97, print_sim_results=False, print_trans_history=False):
  '''
    Parameters:
      mode: train / full / test

    Returns:
      profits, wins, loses 
  '''

  history_log = {'number success': 0,
                'number fails': 0,
                'number wins': 0,
                'proportion': 0,
                'profit': 0,
                'transactions': [] }  
  last_top = df['close'].iloc[0]
  last_top_time = df['close'].index[0]
  last_top_i = 0
  reverse_flag = False
  sell_finished = True
  buy_order_placed = False
  buy_price = 0
  
  if mode == 'train':
    range_ = range(2, int(df.shape[0] * trainig_part))
  if mode == 'full': 
    range_ = range(2,  df.shape[0] - 1)
  if mode == 'test':
    range_ = range(int(df.shape[0] * trainig_part) + 1, df.shape[0] - 1)

  last_top_dict = {'time': [], 'value': []}  

  
  gain_coef = _gain_coef
  lose_coef = _lose_coef
  buy_i = 0 

  for i in range_:
    
    if i >= buy_i:

      if sell_finished == False and df['high'].iloc[i] / buy_price > gain_coef:
        # sell_price = float(df['high'].iloc[i])
        sell_price = buy_price * gain_coef
        history_log['number success'] += 1
        number_buy_stocks = int(buy_money / buy_price)
        history_log['profit'] += (sell_price - buy_price) * number_buy_stocks - commission_value * (sell_price + buy_price) * number_buy_stocks
        history_log['number wins'] += 1
        history_log['transactions'].append({
          'type': 'success',
          'buy_price' : round(buy_price, 2),
          'sell_price': round(sell_price, 2), 
          'ratio': round(buy_ratio_hl ,2),
          'buy_time' : buy_time,
          'sell_time' : df['high'].index[i],
          'buy_lose_coef': buy_lose_coef,
          'buy_gain_coef': buy_gain_coef,
      })
        sell_finished = True
        buy_order_placed = False

      if sell_finished == False and df['low'].iloc[i] / buy_price < lose_coef :
      # sell_price = float(df['low'].iloc[i])
        sell_price = buy_price * lose_coef
        sell_finished = True
        buy_order_placed = True
        number_buy_stocks = int(buy_money / buy_price)
        history_log['profit'] += (sell_price - buy_price) * number_buy_stocks - commission_value * (sell_price + buy_price) * number_buy_stocks
        history_log['number fails'] += 1
        history_log['transactions'].append({
          'type': 'fail',
          'buy_price' : round(buy_price, 2),
          'sell_price': round(sell_price, 2),
          'ratio': round(buy_ratio_hl ,2),
          'buy_time' : buy_time,
          'sell_time' : df['low'].index[i],
          'buy_lose_coef': buy_lose_coef,
          'buy_gain_coef': buy_gain_coef,
        })

    buy_time_cond = True

    # trend is rising: last 120m
    # and number last red candelsis more than 6 out of 8
    # RIV more that 0.02-0.04 ? 

    buy_ratio = float(last_top -  df['open'].iloc[i]) / float(df['ha_pct'].iloc[i] + 0.0001)
    # if df['pct'].iloc[i - 60: i - 1].sum() <= -0.2:
    if df['pct'].iloc[i - 60: i - 1].sum() >= tp \
      and sell_finished == True:
    
      # and df['pct'].iloc[i - 3: i].sum() < 0.1:
    # if df['ha_pct'].iloc[i] > RIV \
    #   and i > 6\
    #   
    #   and buy_time_cond \
    #   and number_red_candles(df,i,k=8) >= nrc  \
    #   and df['ha_colour'].iloc[i - 2] == 'red'\
    #   and df['ha_colour'].iloc[i - 3] == 'red'\
    #   and is_near_global_max(i, k=120, prt=is_near_global_max_prt):

      # and number_red_candles(df,i,k=12) >= 9  \


      # and not(df['close'].iloc[i] > df['close'].iloc[i - 120] \
      # and df['close'].iloc[i] > df['close'].iloc[i - 60] \
      # and df['close'].iloc[i - 60] > df['close'].iloc[i - 120]):
      
    # if i > 6\
    #   and sell_finished == True \
    #   and buy_time_cond \
    #   and is_near_global_max(i, k=240, prt=is_near_global_max_prt) \
    #   and df['ha_pct'].iloc[i] >= 0.02 \
    #   and df['ha_pct'].iloc[i] <= 0.05 \
    #   and df['pct'].iloc[i-30 : i].sum() >= 0.2 \
    #   and df['close'].iloc[i] > df['close'].iloc[i - 120] \
    #   and df['close'].iloc[i] > df['close'].iloc[i - 60] \
    #   and df['close'].iloc[i - 60] > df['close'].iloc[i - 120]:

      #  and df['pct'].iloc[i-30 : i].sum() <= 0.5 \

      # and number_green_candles(df, i, k=8) <=4 \
#  and number_red_candles(df,i,k=8) >= 4 \
      # and is_near_global_max(i, k=120, prt=is_near_global_max_prt):
    
    # if df['ha_pct'].iloc[i] > RIV \
    #   and i > 6\
    #   and sell_finished == True \
    #   and buy_time_cond \
    #   and number_red_candles(df,i,k=8) >= 7  \
    #   and df['ha_colour'].iloc[i - 2] == 'red'\
    #   and df['ha_colour'].iloc[i - 3] == 'red'\
    #   and not is_near_global_max(i, k=120, prt=is_near_global_max_prt):    

      # and global_max_prop(i, 15) > global_max_prop_value:
      # and df['ha_colour'].iloc[i] == 'green'\
      # and df['ha_colour'].iloc[i - 1] == 'green'\
  
      # buy_price = max(df['close'][i - 4 : i])     #best
      # buy_price = min(df['close'].iloc[i - 2: i - 1].min(), df['open'].iloc[i - 2: i - 1].min())
      # buy_price = min(df['close'].iloc[i - 10: i - 1].min(), df['open'].iloc[i - 10: i - 1].min())
      # buy_price = max(df['open'][i - 5 : i])     #best
      buy_price = df['close'].iloc[i] #* 0.998 # 1.0002
   
      buy_time = df.index[i]
      buy_ratio_hl = buy_ratio
      buy_gain_coef = gain_coef
      buy_lose_coef = lose_coef
      # sell_finished = False

    
      # time_inx = df_SP500.index.get_indexer([df.index[i]], method='nearest')[0]
      # if time_inx != 0:
      #   market_value = df_SP500.iloc[time_inx - 60 : time_inx]['pct'].sum()
      # else:
      #   market_value = 0
  
      # if market_value > 0:
      #   buy_order_placed = True
      # else:
      #   buy_order_placed = False
      buy_order_placed = True

      for k in range(2,6):
        if i + k < df.shape[0] - 1:
          if (df['low'].iloc[i + k] < buy_price and df['high'].iloc[i + k] > buy_price):
            sell_finished = False
            buy_i = i + k
            break
      
    # last top and reverse flag
    if df['ha_colour'].iloc[i] == 'red' \
      and df['ha_colour'].iloc[i - 1] == 'green'\
      and df['ha_colour'].iloc[i - 2] == 'green'\
      and df['ha_pct'].iloc[i - 1] > 0.1 \
      and df['ha_pct'].iloc[i - 2] > 0.1:
  
      last_top = df['high'].iloc[i - 1]
      last_top_i = i - 1
      # last_top_dict['time'].append(df.index[i])
      # last_top_dict['value'].append(last_top)
  
  history_log['proportion'] =   history_log['number wins'] / ( history_log['number fails'] + 1)

  # Simulation results 

  if print_sim_results:
    print('-'*50)
    print(f'Simulation results for ticker {ticker}:')
    print(history_log)

    # df_tran = pd.DataFrame(history_log['transactions'])
    # print('Statictic for buy gain coef = 1.02')
    # if df_tran.shape[0] > 0:
    #   print(df_tran.loc[df_tran['buy_gain_coef'] == 1.02]['type'].value_counts())
    #   print(f'Statictic for buy_gain coef = {_gain_coef}')
    #   print(df_tran.loc[df_tran['buy_gain_coef'] == _gain_coef]['type'].value_counts())
    
  if print_trans_history:
    for tran in history_log['transactions']:
      if tran['buy_gain_coef'] == 1.02:
        c.print(tran, color='green')
      else:
        c.print(tran, color='blue')

  return history_log['profit'], history_log['number wins'], history_log['number fails']


In [8]:
buy_time_cond = True
buy_ratio_border = 7
distance_from_last_top  = 0  # NOT SIGNIFICANT?
last_top_ratio = 1.002 # last top / current open price  NOT SIGNIFICANT?
RIV = 0.1 # Reversal indication Value
is_near_global_max_prt = 96 # usd to be 96
bull_trend_coef = 1.12
last_top_24hours_proportion_border = 1

# best_params = {'is_near_global_max_prt': 80, 'distance_from_last_top': 0, 'last_top_ratio': 1, 'RIV': 0.25, 'buy_ratio_border': 9, 'bull_trend_coef': 1.12}
# best_params = {'is_near_global_max_prt': 96, 'distance_from_last_top': 0, 'last_top_ratio': 1.001, 'RIV': 0.15, 'buy_ratio_border': 5, 'bull_trend_coef': 1.12}
# best_params = {'is_near_global_max_prt': 96, 'distance_from_last_top': 0, 'last_top_ratio': 1, 'RIV': 0.15, 'buy_ratio_border': 0, 'bull_trend_coef': 1.12}
# after last check
best_params = {'is_near_global_max_prt': 30, 'distance_from_last_top': 0, 'last_top_ratio': 1, 'RIV': 0.01,
                'buy_ratio_border': 0, 'bull_trend_coef': 1.07, 'last_top_24hours_proportion_border': 1, 'nrc': 7}

for param in best_params:
  vars()[param] = best_params[param]

parameters_list_search = {
  'is_near_global_max_prt' : [0, 20, 30, 50, 70, 80, 96, 100],
  'distance_from_last_top': [0,2,3,5],
  'last_top_ratio': [1, 1.005, 1.01, 1.05, 1.1],
  'RIV' : [0.05, 0.1, 0.15, 0.2, 0.25],
  'buy_ratio_border' : [0,3,5,7,9,10],
  'bull_trend_coef': [1.07, 1.12]
}

parameters_list_search = {
  # 'is_near_global_max_prt' : np.arange(0,100,20),
  # 'is_near_global_max_prt' : [0, 30, 58, 70, 90],
  # 'RIV' : [0.02, 0.05, 0.1, 0.15, 0.2]
  # 'RIV' : np.arange(0, 0.2, 0.01),
  # 'RIV' : [0.01, 0.1, 0.05, 0.12, 0.15, 0.2, 0.3]
  # 'global_max_prop_value': np.arange(1.001,1.01,0.001)
  # 'bull_trend_coef': [1, 1.05, 1.07, 1.12]
  # 'ki': np.arange(2,7,1)
  # 'nrc' : np.arange(2,8,1)
  # 'ni' : np.arange(1,10,1)
  # 'tp': np.arange(-0.4, 0.4, 0.1)
  'tp': np.arange(0.4, 1, 0.1)
}

# {'is_near_global_max_prt': 70, 'distance_from_last_top': 0, 'last_top_ratio': 1.1, 'RIV': 0.2, 'buy_ratio_border': 7, 'bull_trend_coef': 1.07}

# parameters_list_search = {
#   # 'last_top_24hours_proportion_border': np.arange(1, 0, -0.1)
#   'RIV' : [0.05, 0.1, 0.15, 0.2, 0.25]
# }

In [9]:
stock_name_list = []
stock_name_list += ['GOOG','JPM','XOM','UNH','JNJ','V','AVGO','PG','LLY','MA','HD','CVX','MRK', 
                       'PEP','COST','ABBV','ADBE','KO','CRM','WMT','MCD','CSCO','BAC','PFE','TMO','ACN','NFLX','ABT','AMD','LIN','ORCL','CMCSA',
                       'TXN','DIS','WFC','DHR','PM','NEE','VZ','INTC','RTX','HON','LOW','UPS','INTU','SPGI','NKE','COP','QCOM','BMY','CAT','UNP','BA','ISRG',
                        'GE','IBM','AMGN','AMAT','MDT','SBUX','PLD','NOW','MS','DE','BLK','GS','T','LMT','AXP','BKNG','SYK','ADI','TJX','ELV','MDLZ','GILD','ADP','MMC',
                        'C','AMT','CVS','VRTX','SCHW','LRCX','MO','TMUS','SLB', 'ETN', 'ZTS', 'CI', 'PYPL']

stock_name_list += ['FI','CB','SO','REGN','BSX','EQIX','BDX','PANW','DUK','EOG','MU','AON','ITW','CSX','SNPS','PGR','APD','KLAC','CME','NOC','CDNS','ICE','ATVI',
                       'CL','SHW','WM','HCA','TGT','FCX','FDX','F','ORLY','MMM','CMG','EW','GM','MCK','NXPI','MCO','NSC','HUM','EMR','DXCM','PNC','PH','MPC','APH',
                       'ROP','FTNT','MCHP','PXD','USB','CCI','MAR','MSI','GD','PSA','JCI','PSX','SRE','ADSK','AZO','TDG','ECL','AJG','KMB','TEL','TT','AEP','EL','PCAR',
                       'OXY','TFC','CARR','D','IDXX','GIS','ON','COF','ADM','MNST','NUE','CTAS','AIG','EXC','VLO','MRNA','ANET','WMB','O','STZ','IQV','HLT','CHTR','WELL',
                       'BIIB','SPG','MSCI','DHI','ROK']
len(stock_name_list)

191

In [29]:
df['close']

2024-06-17 09:30:00-04:00    177.19
2024-06-17 09:31:00-04:00    177.26
2024-06-17 09:32:00-04:00    177.05
2024-06-17 09:33:00-04:00    177.28
2024-06-17 09:34:00-04:00    176.62
                              ...  
2024-09-12 19:54:00-04:00    156.75
2024-09-12 19:55:00-04:00    156.75
2024-09-12 19:56:00-04:00    156.75
2024-09-12 19:57:00-04:00    156.72
2024-09-12 19:58:00-04:00    156.22
Name: close, Length: 24310, dtype: float64

In [37]:
df['close'].iloc[-6]

np.float64(156.75)

In [47]:
df.index[-1].hour

19

In [38]:
(df['close'].iloc[-6] > df['close'].iloc[-5: -1]).all()

np.True_

In [12]:
# BEST PARAMETERS OPTIMIZATION  and OPTIMAL STOCK LIST
best_profit = -10**5
best_proportion = 0
best_profit_improved = True
optimize_profit = True
optimize_proportion = False
ticker_stats = {}
stock_name_list_opt = stock_name_list[:]
stock_name_list_opt = ['GOOG']
# for parameter in parameters_list_search:
while best_profit_improved:
  for i in random.sample(range(len(parameters_list_search)), len(parameters_list_search)):
    parameter = list(parameters_list_search.keys())[i]
    total_profit_list = []
    total_loses_list = []
    total_proportion_list = []
    for value in parameters_list_search[parameter]:
      vars()[parameter] = value
      c.print(f'parametr is {parameter} value is {value}:', color='white')
      total_profit = 0
      total_loses = 0
      total_wins = 0
      for ticker in stock_name_list_opt:
        file_name = f'df_stock_{ticker}_{file_suffix}'
        path = os.path.join(parent_path, folder_saved_models, file_name)
        df = load_data_one_stock(path)
        ticker_stats[ticker] = {
            'profit': -999,
            'wins': 0,
            'loses' : 0,
        }
        if df.shape[0] > 0:
          # profit, wins, loses= one_stock_simulation(df, ticker, mode='full')
          profit, wins, loses= one_stock_simulation(df, ticker,
                                                     mode='full',
                                                     _gain_coef=1.005,
                                                     _lose_coef=0.995)
          total_profit += profit
          total_loses += loses
          total_wins += wins
          ticker_stats[ticker] = {
            'profit': profit,
            'wins': wins,
            'loses' : loses,
          }
        else:
          stock_name_list_opt.remove(ticker)
      
      total_profit_list.append(total_profit)
      total_loses_list.append(total_loses)
      total_proportion_list.append(total_wins / (total_loses + 1))
      c.print(f'Total Profit is {total_profit:.2f}, total wins is {total_wins}, total loses is {total_loses} \
      proportion {total_wins/(total_loses + 1)}', color = 'red')
      # break if parametr is higher than previous value but profit decreased
      # if len(total_profit_list) > 1:
      #   if total_profit_list[-1] < total_profit_list[-2]:s
      #     break

    c.print(f'total_profit_list: {total_profit_list}', color='orange')
    if optimize_profit:
      vars()[parameter] = parameters_list_search[parameter][np.argmax(total_profit_list)]
    elif optimize_proportion:
      vars()[parameter] = parameters_list_search[parameter][np.argmax(total_proportion_list)]
    else:
      vars()[parameter] = parameters_list_search[parameter][np.argmin(total_loses_list)]
    print(f'parameter {parameter} best value is {vars()[parameter]}')
    # np.max(total_profit_list), np.argmax(total_profit_list)

  parameters_list_best = {}
  for parameter in parameters_list_search:
    print(f'parameter {parameter} best value is {vars()[parameter]}')
    
    parameters_list_best[parameter] = vars()[parameter]
    
  print(parameters_list_best)
  print(max(total_profit_list), min(total_loses_list))

  if optimize_proportion:
    best_profit_improved = max(total_proportion_list) > best_proportion
    best_proportion = max(total_proportion_list) if best_profit_improved else best_proportion
  else:
    best_profit_improved = max(total_profit_list) > best_profit
    best_profit = max(total_profit_list) if best_profit_improved else best_profit

  # Optimization which stocks to use:
  # for ticker in stock_name_list_opt:
  #   if ticker_stats[ticker]['wins'] / (ticker_stats[ticker]['loses'] + 1) < 3 \
  #       or ticker_stats[ticker]['profit'] < 0:
  #     stock_name_list_opt.remove(ticker)
  # c.print(f'Current optimal stock list len is {len(stock_name_list_opt)}, list is {stock_name_list_opt}', color='green')


parametr is tp value is 0.4:
Total Profit is -354.06, total wins is 84, total loses is 87       proportion 0.9545454545454546
parametr is tp value is 0.5:
Total Profit is -285.16, total wins is 69, total loses is 71       proportion 0.9583333333333334
parametr is tp value is 0.6:


KeyboardInterrupt: 

In [ ]:
print(stock_name_list_opt)
# len(stock_name_list_opt)

['GOOG', 'JPM', 'XOM', 'UNH', 'JNJ', 'V', 'AVGO', 'PG', 'LLY', 'MA', 'HD', 'CVX', 'MRK', 'PEP', 'COST', 'ABBV', 'ADBE', 'KO', 'CRM', 'WMT', 'MCD', 'CSCO', 'BAC', 'PFE', 'TMO', 'ACN', 'NFLX', 'ABT', 'AMD', 'LIN', 'ORCL', 'CMCSA', 'TXN', 'DIS', 'WFC', 'DHR', 'PM', 'NEE', 'VZ', 'INTC', 'RTX', 'HON', 'LOW', 'UPS', 'INTU', 'SPGI', 'NKE', 'COP', 'QCOM', 'BMY', 'CAT', 'UNP', 'BA', 'ISRG', 'GE', 'IBM', 'AMGN', 'AMAT', 'MDT', 'SBUX', 'PLD', 'NOW', 'MS', 'DE', 'BLK', 'GS', 'T', 'LMT', 'AXP', 'BKNG', 'SYK', 'ADI', 'TJX', 'ELV', 'MDLZ', 'GILD', 'ADP', 'MMC', 'C', 'AMT', 'CVS', 'VRTX', 'SCHW', 'LRCX', 'MO', 'TMUS', 'SLB', 'ETN', 'ZTS', 'CI', 'PYPL', 'FI', 'CB', 'SO', 'REGN', 'BSX', 'EQIX', 'BDX', 'PANW', 'DUK', 'EOG', 'MU', 'AON', 'ITW', 'CSX', 'SNPS', 'PGR', 'APD', 'KLAC', 'CME', 'NOC', 'CDNS', 'ICE', 'CL', 'SHW', 'WM', 'HCA', 'TGT', 'FCX', 'FDX', 'F', 'ORLY', 'MMM', 'CMG', 'EW', 'GM', 'MCK', 'NXPI', 'NSC', 'HUM', 'EMR', 'DXCM', 'PNC', 'PH', 'MPC', 'APH', 'ROP', 'FTNT', 'MCHP', 'USB', 'CCI', 'MAR'

188

# SOME RESULTS, HISTORY LOG

{'is_near_global_max_prt': 80, 'distance_from_last_top': 2, 'last_top_ratio': 1.001, 'RIV': 0.15, 'buy_ratio_border': 0, 'bull_trend_coef': 1.12}
6056.55094263172 1011
Current optimal stock list len is 127

{'is_near_global_max_prt': 80, 'distance_from_last_top': 2, 'last_top_ratio': 1, 'RIV': 0.15, 'buy_ratio_border': 0, 'bull_trend_coef': 1.12}
7049.139814422607 599
Current optimal stock list len is 99,

{'is_near_global_max_prt': 80, 'distance_from_last_top': 2, 'last_top_ratio': 1, 'RIV': 0.15, 'buy_ratio_border': 10, 'bull_trend_coef': 1.12}
8616.535972952845 423
Current optimal stock list len is 97

{'is_near_global_max_prt': 80, 'distance_from_last_top': 2, 'last_top_ratio': 1, 'RIV': 0.15, 'buy_ratio_border': 0, 'bull_trend_coef': 1.12}
8455.558336365704 662
Current optimal stock list len is 71

v1:
{'is_near_global_max_prt': 80, 'distance_from_last_top': 0, 'last_top_ratio': 1, 'RIV': 0.25, 'buy_ratio_border': 9, 'bull_trend_coef': 1.12}
5762.099450752256 170 , number_red_candles= 6

24/08/2024
{'is_near_global_max_prt': 100, 'distance_from_last_top': 0, 'last_top_ratio': 1, 'RIV': 0.25, 'buy_ratio_border': 0, 'bull_trend_coef': 1.12}
119412.97672809978 380

In [100]:
for parameter in parameters_list_search:
  print(f'parameter {parameter} best value is {vars()[parameter]}')

  # if df['ha_pct'].iloc[i] > RIV \
  # and reverse_flag==False \
  # and sell_finished == True \
  # and last_top / df['open'].iloc[i] > last_top_ratio \
  # and i - last_top_i > distance_from_last_top \
  # and buy_time_cond \
  # and buy_ratio > buy_ratio_border \
  # and not(is_near_global_max(i, k=400, prt=is_near_global_max_prt)):

# Current_optimal_stock_list 
# stock_name_list_opt = ['JPM', 'UNH', 'AVGO', 'HD', 'PEP', 'COST', 'CRM', 'WMT',
#                                 'MCD', 'ABT', 'TXN', 'WFC', 'INTC', 'RTX', 'HON', 'SPGI',
#                                   'BA', 'AMGN', 'AMAT', 'SBUX', 'PLD', 'MS', 'DE', 'AXP', 
#                                   'ADI', 'TJX', 'MMC', 'CVS', 'SCHW', 'TMUS', 'ETN', 'CI', 
#                                   'BSX', 'AON', 'ITW', 'SNPS', 'KLAC', 'CDNS', 'WM', 'HCA',
#                                     'FDX', 'MMM', 'CMG', 'GM', 'MCK', 'NXPI', 'NSC',
#                                       'HUM', 'DXCM', 'PH', 'MPC', 'ROP', 'MCHP', 'MSI', 'GD',
#                                         'JCI', 'SRE', 'ADSK', 'AZO', 'TDG', 'AJG', 'TT', 'PCAR',
#                                           'COF', 'CTAS', 'AIG', 'ANET', 'SPG', 'MSCI', 'ROK']

stock_name_list_opt = [
'BA', 'ON', 'MCHP', 'ADI', 'PANW', 'DHI', 'ANET', 'AMD', 'LRCX', 'LLY',
'MU', 'TXN', 'AIG', 'WMB', 'BSX', 'NKE', 'OXY', 'TT', 'AMAT', 'ETN', 'DE',
'EL', 'FDX', 'MAR', 'GE', 'NFLX', 'NUE', 'GOOG', 'ECL', 'AVGO', 'CAT', 'SPG',
'ADSK', 'INTU', 'SLB', 'F', 'WMT', 'SBUX', 'SNPS', 'AJG', 'TMUS', 'KLAC', 'CI',
'JCI', 'GILD', 'QCOM', 'ROP', 'MO', 'WM', 'HON', 'ITW', 'GS', 'HCA', 'TJX', 'ICE',
'DXCM', 'IDXX', 'ABBV', 'CDNS', 'CMCSA', 'JNJ', 'EQIX', 'MDLZ', 'NXPI', 'MSI', 'TEL',
'LMT', 'USB', 'MRK', 'HLT', 'APD', 'CTAS', 'MNST', 'NOW', 'AMT', 'PH', 'HUM', 'ADM',
'TDG', 'EMR', 'GM', 'ADP', 'CMG', 'SCHW', 'MSCI', 'EOG', 'UNP', 'INTC', 'CME',
'MA', 'CVS', 'XOM', 'CSCO', 'WELL', 'TMO', 'MRNA', 'PLD', 'APH', 'PEP', 'CRM', 'MMM',
'MMC', 'LIN', 'GIS', 'COST', 'CSX', 'IQV', 'FI', 'MCD', 'VRTX'
]

# stock_name_list_opt =['GOOG', 'JPM', 'XOM', 'UNH', 'JNJ', 'V', 'AVGO', 'PG', 'LLY', 'MA', 'HD', 'CVX', 'MRK', 'PEP', 'COST', 'ABBV', 'ADBE', 'KO', 'CRM', 'WMT', 'MCD', 'CSCO', 'BAC', 'PFE', 'TMO', 'ACN', 'NFLX', 'ABT', 'AMD', 'LIN', 'ORCL', 'CMCSA', 'TXN', 'DIS', 'WFC', 'DHR', 'PM', 'NEE', 'VZ', 'INTC', 'RTX', 'HON', 'LOW', 'UPS', 'INTU', 'SPGI', 'NKE', 'COP', 'QCOM', 'BMY', 'CAT', 'UNP', 'BA', 'ISRG', 'GE', 'IBM', 'AMGN', 'AMAT', 'MDT', 'SBUX', 'PLD', 'NOW', 'MS', 'DE', 'BLK', 'GS', 'T', 'LMT', 'AXP', 'BKNG', 'SYK', 'ADI', 'TJX', 'ELV', 'MDLZ', 'GILD', 'ADP', 'MMC', 'C', 'AMT', 'CVS', 'VRTX', 'SCHW', 'LRCX', 'MO', 'TMUS', 'SLB', 'ETN', 'ZTS', 'CI', 'PYPL', 'FI', 'CB', 'SO', 'REGN', 'BSX', 'EQIX', 'BDX', 'PANW', 'DUK', 'EOG', 'MU', 'AON', 'ITW', 'CSX', 'SNPS', 'PGR', 'APD', 'KLAC', 'CME', 'NOC', 'CDNS', 'ICE', 'CL', 'SHW', 'WM', 'HCA', 'TGT', 'FCX', 'FDX', 'F', 'ORLY', 'MMM', 'CMG', 'EW', 'GM', 'MCK', 'NXPI', 'NSC', 'HUM', 'EMR', 'DXCM', 'PNC', 'PH', 'MPC', 'APH', 'ROP', 'FTNT', 'MCHP', 'USB', 'CCI', 'MAR', 'MSI', 'GD', 'PSA', 'JCI', 'PSX', 'SRE', 'ADSK', 'AZO', 'TDG', 'ECL', 'AJG', 'KMB', 'TEL', 'TT', 'AEP', 'EL', 'PCAR', 'OXY', 'TFC', 'CARR', 'D', 'IDXX', 'GIS', 'ON', 'COF', 'ADM', 'MNST', 'NUE', 'CTAS', 'AIG', 'EXC', 'VLO', 'MRNA', 'ANET', 'WMB', 'O', 'STZ', 'IQV', 'HLT', 'CHTR', 'WELL', 'BIIB', 'SPG', 'MSCI', 'DHI', 'ROK']


len(stock_name_list_opt), len(stock_name_list)


parameter is_near_global_max_prt best value is 96
parameter distance_from_last_top best value is 0
parameter last_top_ratio best value is 1.01
parameter RIV best value is 0.05
parameter buy_ratio_border best value is 0
parameter bull_trend_coef best value is 1.07


(110, 188)

In [21]:
len(stock_name_list), len(stock_name_list_opt)

(188, 187)

In [130]:
# TRY TO REDUCE NUMBER OF FAIL NOT PROFIT!!!
total_profit_list = []
# parametr_list = np.arange(86, 100, 1)
# parametr_list = [1, 1.001, 1.002, 1.005, 1.007, 1.01, 1.02]
# parametr_list = [30]
# for p in parametr_list:
#   is_near_global_max_prt= p
 
# print("TRAIN RESULTS")
# total_profit = 0
# total_loses = 0
# total_wins = 0
# for ticker in stock_name_list_opt:
#   file_name = f'df_stock_{ticker}_period2y_interval1h.pkl'
#   path = os.path.join(parent_path, folder_saved_models, file_name)
#   df = load_data_one_stock(path)
#   profit, wins, loses = one_stock_simulation(df, ticker, mode = 'train', print_sim_results=True, print_trans_history=False)
#   total_profit += profit
#   total_loses += loses
#   total_wins += wins
# print(f'Total Profit is {total_profit:.2f}, total loses is {total_loses}, total wins is {total_wins}, proportion: {total_wins / total_loses + 1:.2f}')

print("TEST RESULTS")
total_profit = 0
total_loses = 0
total_wins = 0
for ticker in stock_name_list_opt:
# for ticker in stock_name_list:
  file_name = f'df_stock_{ticker}_{file_suffix}'
  path = os.path.join(parent_path, folder_saved_models, file_name)
  df = load_data_one_stock(path)
  if df.shape[0] > 0:
    profit, wins, loses = one_stock_simulation(df, ticker, mode = 'test', print_sim_results=False, print_trans_history=False)
    total_profit += profit
    total_loses += loses
    total_wins += wins
    print(f'Total Profit is {total_profit:.2f}, total loses is {total_loses}, total wins is {total_wins}, proportion: {total_wins / (total_loses + 1):.2f}')
  else:
    print(f'{ticker} empty df')


TEST RESULTS
[Errno 2] No such file or directory: 'f:\\Git Projects\\HeikenAshiInvestingModel\\historical_data\\periodmaxinterval1m\\df_stock_GOOG_period2y_interval1h.pkl'
GOOG empty df
[Errno 2] No such file or directory: 'f:\\Git Projects\\HeikenAshiInvestingModel\\historical_data\\periodmaxinterval1m\\df_stock_JPM_period2y_interval1h.pkl'
JPM empty df
[Errno 2] No such file or directory: 'f:\\Git Projects\\HeikenAshiInvestingModel\\historical_data\\periodmaxinterval1m\\df_stock_XOM_period2y_interval1h.pkl'
XOM empty df
[Errno 2] No such file or directory: 'f:\\Git Projects\\HeikenAshiInvestingModel\\historical_data\\periodmaxinterval1m\\df_stock_UNH_period2y_interval1h.pkl'
UNH empty df
[Errno 2] No such file or directory: 'f:\\Git Projects\\HeikenAshiInvestingModel\\historical_data\\periodmaxinterval1m\\df_stock_JNJ_period2y_interval1h.pkl'
JNJ empty df
[Errno 2] No such file or directory: 'f:\\Git Projects\\HeikenAshiInvestingModel\\historical_data\\periodmaxinterval1m\\df_stock_V

In [239]:
# best_params = {'is_near_global_max_prt': 96, 'distance_from_last_top': 0, 'last_top_ratio': 1, 'RIV': 0.05, 'buy_ratio_border': 0, 'bull_trend_coef': 1.07}
# best_params = {'is_near_global_max_prt': 30, 'distance_from_last_top': 0, 'last_top_ratio': 1.1, 'RIV': 0.1, 'buy_ratio_border': 0, 'bull_trend_coef': 1.07}
# best_params = {'is_near_global_max_prt': 20, 'distance_from_last_top': 0, 'last_top_ratio': 1.1, 'RIV': 0.05, 'buy_ratio_border': 0, 'bull_trend_coef': 1.07}
# best_params = {'is_near_global_max_prt': 70, 'distance_from_last_top': 0, 'last_top_ratio': 1.1, 'RIV': 0.2, 'buy_ratio_border': 7, 'bull_trend_coef': 1.07}
best_params = {'is_near_global_max_prt': 30, 'distance_from_last_top': 0, 'last_top_ratio': 1, 'RIV': 0.2, 'buy_ratio_border': 0, 'bull_trend_coef': 1.07,
              'is_near_global_max_prt2': 60,  'global_max_prop_ratio' : 1.08, 'tp' : 0.5}
for param in best_params:
  vars()[param] = best_params[param]

stock_name_list_opt = ['DXCM', 'BIIB', 'CCI', 'CVS', 'WFC', 'CSX', 'TXN', 'HD', 'DUK', 'ABBV', 'KO',
                        'PSA', 'BA', 'PYPL', 'SBUX', 'ADM', 'FDX', 'PGR', 'ADP', 'JCI', 'TEL', 'WM', 'IDXX',
                          'NUE', 'ITW', 'PCAR', 'SPG', 'BDX', 'PEP', 'KMB', 'ROK', 'DE', 'AMGN', 'MNST', 'SNPS', 
                          'CL', 'MMC', 'BLK', 'AJG', 'MDLZ', 'AMD', 'CB', 'SCHW', 'AVGO', 'WELL', 'MSCI', 'MRNA', 
                          'OXY', 'ADSK', 'APH', 'IBM', 'CHTR', 'EL', 'MDT', 'GS', 'NOC', 'ELV', 'USB', 'AEP', 'SRE',
                            'LMT', 'LIN', 'WMT', 'TT', 'PSX', 'UNP', 'MCD', 'CMG', 'ROP', 'QCOM', 'CVX', 'SO', 'NEE', 
                            'UNH', 'CDNS', 'AXP', 'MRK', 'CMCSA', 'MO', 'ORCL', 'NFLX', 'MPC', 'FTNT', 'MU', 'ECL',
                              'JPM', 'SHW', 'CSCO', 'ETN', 'GOOG', 'SYK', 'MCHP']

In [240]:
print("FULL RESULTS OPTIMIZATION")
# parameters:
lose_coef = 0.998
gain_coef = 1.002
mode = 'full'
# gain_coef = 1.02
use_optimal_stock_list = False
use_stock_name_list_selected = False
#
total_profit = 0
total_loses = 0
total_wins = 0

if use_optimal_stock_list:
  current_stock_name_list = stock_name_list_opt[:]
else:
  current_stock_name_list = stock_name_list[:]

if use_stock_name_list_selected:
  current_stock_name_list = stock_name_list_selected[:]

# current_stock_name_list = ['GOOG']

df_opt = pd.DataFrame(columns=['ticker','profit', 'wins', 'loses', 'proportion'])

for ticker in current_stock_name_list:
# for ticker in ['Avgo']:
  file_name = f'df_stock_{ticker}_{file_suffix}'
  path = os.path.join(parent_path, folder_saved_models, file_name)
  df = load_data_one_stock(path)

  # if ticker in opt_stocks_for_bear_trend:
  #   gain_coef = 1.02
  # else:
  #   gain_coef = 1.005

  if df.shape[0] > 0:
    profit, wins, loses = one_stock_simulation(df, ticker,
                                               mode=mode,
                                               _gain_coef=gain_coef,
                                               _lose_coef=lose_coef, 
                                               print_sim_results=True,
                                               print_trans_history=False)
    if loses == 0:
      proportion = wins
    else:
      proportion = wins / loses
    df2 = pd.DataFrame({'ticker': [ticker],'profit': [profit], 'wins': [wins], 'loses': [loses], 'proportion': [proportion]})
    df_opt = pd.concat([df_opt, df2], ignore_index=True)
    total_profit += profit
    total_loses += loses
    total_wins += wins
    if total_loses == 0:
      total_proportion = total_wins
    else:
      total_proportion = total_wins / total_loses
  else:
    print(f'{ticker} empty df')
c.print(f'Total Profit is {total_profit:.2f}, total loses is {total_loses}, total wins is {total_wins}, proportion: {total_proportion:.2f}', color = 'blue')
c.print('Parameters are:', color = 'blue' )
c.print(f'gain_coef is {gain_coef}; lose_coef is {lose_coef}; use_optimal_stock_list is {use_optimal_stock_list}, use_selected_optimal_stock_list is \
{use_stock_name_list_selected} mode is {mode}', color = 'blue')
for param in best_params:
   print(f'{param} is {vars()[param]}')

FULL RESULTS OPTIMIZATION
--------------------------------------------------
Simulation results for ticker GOOG:
{'number success': 78, 'number fails': 70, 'number wins': 78, 'proportion': 1.0985915492957747, 'profit': np.float64(-252.51873275999878), 'transactions': [{'type': 'success', 'buy_price': np.float64(178.17), 'sell_price': np.float64(178.53), 'ratio': 42.97, 'buy_time': Timestamp('2024-06-17 12:59:00-0400', tz='US/Eastern'), 'sell_time': Timestamp('2024-06-17 13:14:00-0400', tz='US/Eastern'), 'buy_lose_coef': 0.998, 'buy_gain_coef': 1.002}, {'type': 'fail', 'buy_price': np.float64(179.57), 'sell_price': np.float64(179.21), 'ratio': -130.91, 'buy_time': Timestamp('2024-06-17 14:08:00-0400', tz='US/Eastern'), 'sell_time': Timestamp('2024-06-17 14:18:00-0400', tz='US/Eastern'), 'buy_lose_coef': 0.998, 'buy_gain_coef': 1.002}, {'type': 'success', 'buy_price': np.float64(179.5), 'sell_price': np.float64(179.86), 'ratio': 10.14, 'buy_time': Timestamp('2024-06-21 09:55:00-0400', tz

C:\Users\IvanSpok\AppData\Local\Temp\ipykernel_12264\2891197087.py:49: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_opt = pd.concat([df_opt, df2], ignore_index=True)


--------------------------------------------------
Simulation results for ticker JPM:
{'number success': 66, 'number fails': 52, 'number wins': 66, 'proportion': 1.2452830188679245, 'profit': np.float64(-169.96044447000006), 'transactions': [{'type': 'fail', 'buy_price': np.float64(197.01), 'sell_price': np.float64(196.62), 'ratio': 53.39, 'buy_time': Timestamp('2024-06-18 10:02:00-0400', tz='US/Eastern'), 'sell_time': Timestamp('2024-06-18 10:07:00-0400', tz='US/Eastern'), 'buy_lose_coef': 0.998, 'buy_gain_coef': 1.002}, {'type': 'fail', 'buy_price': np.float64(196.86), 'sell_price': np.float64(196.47), 'ratio': -1.34, 'buy_time': Timestamp('2024-06-18 10:08:00-0400', tz='US/Eastern'), 'sell_time': Timestamp('2024-06-18 10:24:00-0400', tz='US/Eastern'), 'buy_lose_coef': 0.998, 'buy_gain_coef': 1.002}, {'type': 'fail', 'buy_price': np.float64(196.74), 'sell_price': np.float64(196.35), 'ratio': -1.5, 'buy_time': Timestamp('2024-06-18 10:24:00-0400', tz='US/Eastern'), 'sell_time': Timest

Results:
1. use ordered selected stock list;
2. Use danamic gain coeficient'


In [121]:
df_opt = df_opt.sort_values(by='profit', ascending=False)
print(df_opt)
# df_opt.to_csv('df_opt.csv')

   ticker      profit wins loses  proportion
74   CDNS  267.436113   67     0   67.000000
83     MU  246.080424   66     2   33.000000
64    PSX  244.948723   68     0   68.000000
69   QCOM  233.681065   60     0   60.000000
81    MPC  228.595442   68     0   68.000000
..    ...         ...  ...   ...         ...
76    MRK -136.243427    9    30    0.300000
58    AEP -166.474707    0    30    0.000000
77  CMCSA -170.790966    2    30    0.066667
28    PEP -177.056994    0    33    0.000000
79   ORCL -253.189184    1    43    0.023256

[92 rows x 5 columns]


In [50]:
stock_name_list_selected = df_opt.loc[df_opt['profit'] > 0].sort_values(by='profit', ascending=False)['ticker']
print(stock_name_list_selected.to_list())
print(len(stock_name_list_selected))
# stock_name_for_check = [
# 'BA', 'ON', 'MCHP', 'ADI', 'PANW', 'DHI', 'ANET', 'AMD', 'LRCX', 'LLY',
# 'MU', 'TXN', 'AIG', 'WMB', 'BSX', 'NKE', 'OXY', 'TT', 'AMAT', 'ETN', 'DE',
# 'EL', 'FDX', 'MAR', 'GE', 'NFLX', 'NUE', 'GOOG', 'ECL', 'AVGO', 'CAT', 'SPG',
# 'ADSK', 'INTU', 'SLB', 'F', 'WMT', 'SBUX', 'SNPS', 'AJG', 'TMUS', 'KLAC', 'CI',
# 'JCI', 'GILD', 'QCOM', 'ROP', 'MO', 'WM', 'HON', 'ITW', 'GS', 'HCA', 'TJX', 'ICE',
# 'DXCM', 'IDXX', 'ABBV', 'CDNS', 'CMCSA', 'JNJ', 'EQIX', 'MDLZ', 'NXPI', 'MSI', 'TEL',
# 'LMT', 'USB', 'MRK', 'HLT', 'APD', 'CTAS', 'MNST', 'NOW', 'AMT', 'PH', 'HUM', 'ADM',
# 'TDG', 'EMR', 'GM', 'ADP', 'CMG', 'SCHW', 'MSCI', 'EOG', 'UNP', 'INTC', 'CME',
# 'MA', 'CVS', 'XOM', 'CSCO', 'WELL', 'TMO', 'MRNA', 'PLD', 'APH', 'PEP', 'CRM', 'MMM',
# 'MMC', 'LIN', 'GIS', 'COST', 'CSX', 'IQV', 'FI', 'MCD', 'VRTX'
# ]
# (stock_name_for_check == stock_name_list_selected).all()
opt_stocks_for_bear_trend = ['BA', 'INTU', 'MCHP', 'LLY', 'DHI', 'ANET', 'AIG', 'NUE', 'MAR', 'OXY', 'ON',
  'GE', 'AMAT', 'NXPI', 'SNPS', 'UNP', 'KLAC', 'BSX', 'MSI', 'CRM', 'CAT', 'ADI',
    'ETN', 'JCI', 'HLT', 'CSCO', 'WMT', 'TDG', 'TT', 'ECL', 'LOW', 'ADSK', 'TJX',
    'VRTX', 'APH', 'ABBV', 'STZ', 'SBUX', 'DE', 'MRK', 'CTAS', 'MNST', 'CME', 'MO', 'TXN', 'ITW']
# print(stock_name_list_selected)
# df_opt.loc[df_opt['profit'] > 0].sort_values(by='profit', ascending=False)


['BMY', 'SBUX', 'CMG', 'ADI', 'QCOM', 'BAC', 'NSC', 'NKE', 'COST', 'TMUS', 'AJG', 'AXP', 'NXPI', 'ACN', 'ECL', 'VLO', 'IBM', 'ON', 'FTNT', 'EW', 'AVGO', 'TJX', 'WELL', 'BDX', 'LLY', 'XOM', 'CL', 'LIN', 'ZTS', 'AMT', 'MAR', 'BLK', 'FDX', 'JPM', 'MCD', 'MPC', 'KMB', 'CME', 'LMT', 'CB', 'KLAC', 'CDNS', 'AON', 'TMO', 'ADBE', 'MCK', 'IQV', 'ITW', 'UNP', 'JCI', 'GIS', 'F', 'MNST', 'O', 'C', 'EXC', 'KO', 'WMT', 'AEP', 'ABBV', 'GM', 'PGR', 'PM', 'MCHP', 'VRTX', 'CMCSA', 'WFC', 'ICE', 'MCO', 'D', 'ISRG', 'STZ', 'USB', 'RTX', 'TGT', 'PSX', 'MA', 'EMR', 'MDLZ', 'GILD', 'MRK', 'MS', 'MMM', 'EOG', 'CCI', 'DUK', 'MMC', 'ABT', 'PNC', 'ETN', 'GD', 'BA', 'MSI', 'COF', 'GE', 'FI', 'PG', 'SPG', 'TXN', 'ADP', 'HON', 'V', 'CRM', 'CTAS', 'CI', 'CHTR', 'SYK', 'ANET', 'PSA', 'INTU', 'UNH', 'MSCI', 'ROP', 'ELV', 'NOC', 'GS', 'SPGI']
117


In [ ]:
df_opt_bear_trend = df_opt.sort_values(by='proportion', ascending=False)

df_opt_bear_trend = df_opt_bear_trend.loc[df_opt_bear_trend['proportion'] >= 3].sort_values(by='profit', ascending=False)
print(df_opt_bear_trend)
print(df_opt_bear_trend['ticker'].to_list())